In [1]:
import pandas as pd 

data = pd.read_csv("Corona_NLP_train.csv", encoding = 'latin1') 
data.head()

UserName  ScreenName   Location     TweetAt  \
0      3799       48751     London  16-03-2020   
1      3800       48752         UK  16-03-2020   
2      3801       48753  Vagabonds  16-03-2020   
3      3802       48754        NaN  16-03-2020   
4      3803       48755        NaN  16-03-2020   

                                       OriginalTweet           Sentiment  
0  @MeNyrbie @Phil_Gahan @Chrisitv https://t.co/i...             Neutral  
1  advice Talk to your neighbours family to excha...            Positive  
2  Coronavirus Australia: Woolworths to give elde...            Positive  
3  My food stock is not the only one which is emp...            Positive  
4  Me, ready to go at supermarket during the #COV...  Extremely Negative

In [2]:
data = data.drop(['UserName', 'ScreenName', 'Location', 'TweetAt'], axis = 1)
data.head()

OriginalTweet           Sentiment
0  @MeNyrbie @Phil_Gahan @Chrisitv https://t.co/i...             Neutral
1  advice Talk to your neighbours family to excha...            Positive
2  Coronavirus Australia: Woolworths to give elde...            Positive
3  My food stock is not the only one which is emp...            Positive
4  Me, ready to go at supermarket during the #COV...  Extremely Negative

In [11]:
import re
import preprocessor.api as p
from contractions import contractions_dict
from nltk.corpus import wordnet
import pattern
from pattern.en import suggest, lemma
import wordninja
from numpy import nan
from nltk.tokenize import word_tokenize
import nltk
from stopword import stopwords
from nltk.corpus import words
from tqdm._tqdm_notebook import tqdm_notebook


def remove_nonASCII(text):
    #remove non english alphabet
    return re.sub(r'[^\x00-\x7f]',"", text)

def remove_repeated_characters(word):
    pattern = re.compile(r"(\w*)(\w)\2(\w*)")
    substitution_pattern = r"\1\2\3"
    while True:
        if wordnet.synsets(word):
            return word
        new_word = pattern.sub(substitution_pattern,word)
        if new_word != word:
            word = new_word
            continue
        else:
            return new_word

def expand_contractions(text):
    pattern = re.compile("({})".format("|".join(contractions_dict.keys())),flags = re.DOTALL| re.IGNORECASE)
    
    def replace_text(t):
        txt = t.group(0)
        if txt.lower() in contractions_dict.keys():
            return contractions_dict[txt.lower()]
        
    expand_text = pattern.sub(replace_text,text)
    return expand_text 

def spelling_checker(word):
    checker = suggest(word)
    return checker[0][0]

def remove_stopwords(w):
    text = []
    for word in w:
        if word not in stopwords:
              text.append(word)
    return text

def split_words(words):
    #split words which are not separated by space
    wlist = []
    for word in words:
        # 12 is decided based on distribution of word length in English
        if len(word)> 12:
            wlist = wlist + wordninja.split(word)
        else:
            wlist.append(word)
    return wlist

def preprocess_unit(text):
    text = remove_nonASCII(text)
    text = re.sub('\S+@\S*\s?', ' ', text) #remove email
    text = p.clean(text)    # remove URL, hashtag, @-mention, emojis
    text = re.sub(r'[^\w\s]', ' ', text) #remove punctuations
    text = re.sub(r'\_','',text) #remove underscore
    text = re.sub(r'[0-9]+', '', text) #remove digits
    text = text.lower() #to lower case
    text = expand_contractions(text) #expand contraction
    Words = word_tokenize(text) #tokenization
    filtered_words = remove_stopwords(Words) #remove stopwords
    if len(filtered_words) > 0:
        """
        for word in filtered_words:
            if word in words.words():
                output.append(word)
            else:
                output.append(remove_repeated_characters(word))
        """
        #output = split_words(output)
        output = [spelling_checker(s) for s in filtered_words]
        output = [lemma(s) for s in output]
        print(output)
        return output
    else:
        return nan

#tqdm_notebook.pandas()
data['tokens'] = data['OriginalTweet'].progress_apply(preprocess_unit)
data.head()
data.to_csv("preprocess_train.csv", index = False, header = True)

['advice', 'talk', 'neighbour', 'family', 'exchange', 'phone', 'number', 'create', 'contact', 'list', 'phone', 'number', 'neighbour', 'school', 'employer', 'chemist', 'up', 'set', 'online', 'shop', 'account', 'pass', 'adequate', 'supply', 'regular', 'bed', 'not', 'order']
['coronaviru', 'australia', 'woolworth', 'give', 'elderly', 'disable', 'dedicate', 'shop', 'hour', 'amid', 'can', 'outbreak']
['food', 'stock', 'not', 'one', 'empty', 'please', 'panic', 'enough', 'food', 'everyone', 'not', 'take', 'need', 'stay', 'calm', 'stay', 'safe']
['ready', 'go', 'superb', 'outbreak', 'not', 'paranoid', 'food', 'stock', 'literary', 'empty', 'seriou', 'thing', 'please', 'panic', 'cause', 'shortage']
['new', 'region', 'first', 'confirm', 'can', 'case', 'come', 'sullivan', 'county', 'last', 'week', 'people', 'flock', 'area', 'store', 'purchase', 'clean', 'supply', 'hand', 'sanitizer', 'food', 'toilet', 'paper', 'good', 'report']
['cashier', 'grocer', 'store', 'share', 'insight', 'prove', 'credibili

['global', 'food', 'price', 'spread', 'can', 'intensify', 'acros', 'several', 'biography', 'can', 'see', 'downward', 'pressure', 'come', 'month', 'due', 'continue', 'well', 'supply', 'it', 'negative', 'impact', 'demand', 'result', 'viru']
['morn', 'everyone', 'great', 'safe', 'day']
['thing', 'panic', 'buy', 'emergency', 'get', 'toilet', 'paper', 'important', 'afraid', 'worst', 'case', 'scenario', 'wash', 'tub', 'use', 'money', 'food', 'crazy']
['thank', 'grocer', 'clerk', 'go', 'grocer', 'store', 'today', 'look', 'weary', 'eye', 'clerk', 'thank', 'realize', 'thrust', 'front', 'line', 'panic', 'new', 'breed', 'first', 'respond', 'work', 'hard', 'serve', 'community']
['outbreak', 'can', 'entire', 'world', 'retail', 'shop', 'malasha', 'face', 'great', 'challenge', 'near', 'future', 'online', 'shop', 'surprise', 'way', 'people', 'many', 'lose', 'job']
['thought', 'impart', 'coronaviru', 'food', 'it']
['consumer', 'corner', 'take', 'advantage', 'fear']
['mass', 'make', 'medical', 'personne

['also', 'need', 'say', 'go', 'grocer', 'store', 'not', 'do', 'completely', 'safely', 'mean', 'without', 'risk', 'get', 'spread', 'reduce', 'risk', 'stay', 'ft', 'people', 'amp', 'wash', 'hand', 'eliminate']
['maybe', 'come', 'recession', 'might', 'play', 'three', 'phase', 'damage', 'main', 'street', 'can', 'go', 'c', 'rescue', 'hemp', 'recovery', 'credit', 'meet', 'no', 'recovery', 'consumer', 'icon', 'unknown', 'second', 'shock', 'later', 'finally', 'bring', 'wall', 'street', 'altogether', 'six', 'rut', 'nd']
['know', 'end', 'world', 'surgical', 'spirit', 'stock', 'online', 'receive', 'stock', 'suppose', 'disinfect', 'hand']
['get', 'real', 'world', 'know', 'real', 'many', 'world', 'please', 'sign', 'petition', 'food', 'be', 'people', 'colorado']
['amid', 'social', 'distend', 'can', 'crisi', 'starbuck', 'move', 'go']
['aniline', 'bar', 'feel', 'economic', 'impact', 'can']
['update', 'make', 'sure', 'check', 'local', 'list', 'see', 'open', 'close', 'time', 'thick', 'fig', 'drive', 'st

['would', 'list', 'plethoric', 'do', 'unfortunately', 'day', 'job', 'health', 'care', 'superb', 'retail', 'everyone', 'tuck', 'ill', 'take', 'care', 'sick', 'fee', 'hungry']
['thing', 'may', 'stock', 'thing', 'get', 'crazy', 'chocolate', 'make', 'remove', 'conceal', 'dark', 'circle', 'chew', 'gum', 'pringle', 'seed', 'grow', 'flower', 'manual', 'survive', 'apocalypse', 'chocolate', 'gin', 'kitten', 'heel', 'shoe']
['please', 'read', 'full', 'lava', 'can', 'statement', 'amp', 'announcement', 'online', 'store', 'consumer', 'electronic', 'compute', 'interface']
['cleanshelf', 'superb', 'sanitizer']
['increase', 'worker', 'online', 'shop', 'add', 'time', 'shot', 'pick', 'delivery', 'hire', 'worker', 'short', 'time', 'busines', 'shut']
['thank', 'take', 'care', 'abuelo']
['also', 'people', 'stock', 'soap', 'hand', 'sanitiser', 'toilet', 'roll', 'leave', 'shelve', 'empty', 'rest', 'u', 'realise', 'stop', 'spread', 'people', 'need', 'able', 'wash', 'hand']
['nearly', 'year', 'old', 'anna', 'h

['hear', 'multiple', 'source', 'mandatory', 'quarante', 'come', 'week', 'u', 'citizen', 'last', 'chance', 'stock', 'food', 'amp', 'supply', 'take', 'warn', 'late']
['stock', 'drop', 'amid', 'can', 'outbreak', 'latest', 'extent', 'damage', 'share', 'price', 'several', 'key', 'company', 'teach', 'amp', 'media', 'auto', 'amp', 'transportation', 'travel', 'retail', 'amp', 'consumer', 'good', 'draft', 'amp', 'finance', 'opportunity', 'invest']
['lot', 'u', 'go', 'self', 'isolation', 'week', 'think', 'useful', 'article', 'stay', 'sane', 'happy']
['panic', 'buy', 'malasha', 'excavate', 'today', 'follow', 'rumour', 'impend', 'lockdown', 'ministry', 'domestic', 'trade', 'consumer', 'affair', 'warn', 'people', 'not', 'spread', 'face', 'new', 'can', 'warman', 'yusoff', 'amp', 'shafwan', 'pardon']
['increasingly', 'global', 'spread', 'can', 'mass', 'begin', 'panic', 'grocer', 'store', 'become', 'increasingly', 'chronic', 'animalistic', 'nature', 'survival', 'kick', 'individual', 'start', 'hoard', 

...

['people', 'food', 'requirement', 'change', 'can', 'buy', 'habit', 'people', 'would', 'stop', 'panic', 'buy', 'hard', 'would', 'no', 'empty', 'shelve', 'store', 'people', 'need', 'stop', 'pack', 'stop', 'selfish']
['live', 'bourbon', 'community', 'roundtable', 'discuss', 'can', 'change', 'consumer', 'demand', 'indefinitely', 'large', 'beverage', 'organization', 'can', 'by', 'he', 'really', 'mean', 'everyone', 'else', 'c', 'mon', 'join']
['hillsborough', 'county', 'sheriff', 'have', 'chronicler', 'talk', 'recent', 'effect', 'quarante', 'resident', 'deal', 'consumer', 'quarterback', 'show', 'iheartradio', 'weekday', 'clock', 'drive', 'time', 'answer', 'sunday', 'be', 'bone']
['many', 'face', 'financial', 'uncertainty', 'time', 'consumer', 'financial', 'protection', 'bureau', 'site', 'list', 'key', 'resource', 'step', 'help', 'protect', 'financially', 'impact', 'can']
['let', 'urge', 'african', 'government', 'quadruple', 'support', 'farmer', 'ensure', 'food', 'sovereignty', 'food', 'price

['disperse', 'tell', 'pp', 'believe', 'see', 'tender', 'call', 'calf', 'price', 'correct', 'since', 'go', 'guess', 'see', 'come', 'somehow', 'predict', 'back']
['current', 'monthly', 'budget']
['digital', 'eat', 'initiative', 'constrain', 'pause', 'due', 'budget', 'cut', 'online', 'retainer', 'average', 'cost', 'effective', 'value', 'ever', 'help', 'reach', 'today', 'consumer', 'fuel', 'online', 'revenue', 'growth']
['face', 'bring', 'tm', 'suit', 'company', 'inflation', 'price', 'mass', 'need', 'ever', 'be']
['freeze', 'consumer', 'habit']
['boast', 'gas', 'price', 'stone-wall', 'u', 'post', 'office', 'aid']
['pm', 'mode', 'no', 'need', 'worry', 'essential', 'india', 'enough', 'stock', 'everythe', 'food', 'medicine']
['pm', 'address', 'nation', 'l', 'announce', 'lockdown', 'extension', 'amid', 'coronaviru', 'outbreak']
['can', 'up', 'wind', 'turbine', 'price', 'increase', 'renew', 'renewal', 'energy', 'new']
['western', 'canada', 'pulse', 'feather', 'impart', 'can', 'anaemic', 'relati

['work', 'feet', 'work', 'extra', 'day', 'week', 'extra', 'hour', 'every', 'day', 'receive', 'no', 'extra', 'pay', 'give', 'u', 'mass', 'glove', 'clorox', 'wipe', 'hand', 'sanitizer', 'feet', 'make', 'shitload', 'money', 'employee', 'receive', 'nothe']
['much', 'global', 'growth', 'fall', 'result', 'collapse', 'oil', 'price', 'outlook', 'economic', 'recovery', 'learn', 'rec']
['wife', 'online', 'shop', 'turn', 'super', 'excite', 'say', 'buy', 'sandwich', 'maker', 'confuse', 'really', 'dont', 'think', 'afford', 'another', 'woman', 'home']
['curiou', 'thing', 'grocer', 'store', 'be', 'target', 'lower', 'home', 'depot', 'employee', 'infect', 'neck', 'drop', 'like', 'fly', 'bad', 'point', 'store', 'unable', 'operate', 'lack', 'employee']
['come', 'can', 'crisi', 'consumer', 'busines', 'need', 'strategically', 'plan', 'temporary', 'economic', 'shutdown', 'akin', 'draft', 'industry', 'experience', 'stress', 'test', 'post']
['think', 'buy', 'habit', 'temporary', 'not', 'change', 'future', 'ca

['ask', 'price', 'house', 'canberra', 'continue', 'rise', 'despite', 'economic', 'impart', 'can', 'emergency', 'canberra', 'experience', 'second', 'largest', 'increase', 'property', 'list', 'nation', 'h']
['be', 'farmer', 'dump', 'milk', 'break', 'egg', 'restaurant', 'close', 'destroy', 'demand', 'close', 'hospitality', 'industry', 'affect', 'farmer', 'ches', 'acros', 'america', 'heartbreak', 'reality', 'supply', 'chain', 'amid']
['airline', 'offer', 'fewer', 'choice', 'expensive', 'price', 'post', 'first', 'get', 'consumer', 'trust', 'travel']
['read', 'distributor', 'like', 'price', 'front', 'run', 'can', 'drug', 'demand', 'spike']
['suppose', 'test', 'can', 'today', 'weather', 'massachusett', 'bad', 'high', 'wind', 'amp', 'lot', 'heavy', 'rain', 'get', 'test', 'tomorrow', 'grocer', 'employee', 'amp', 'grocer', 'store', 'employee', 'massachusett', 'recommend', 'get', 'test', 'amp', 'free']
['tell', 'mon', 'amp', 'dad', 'get', 'test', 'tomorrow', 'can', 'manager', 'grocer', 'store', '

['well', 'new', 'used', 'rift', 'go', 'amazon', 'in', 'although', 'normal', 'et', 'price', 'usually', 'price', 'really', 'crazy', 'right', 'or', 'headset', 'since', 'he', 'flex', 'announce', 'worse', 'can', 'whether']

